In [ ]:
import numpy as np
import pandas as pd
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler, LabelEncoder, MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
df1 = pd.read_csv('/content/drive/MyDrive/Datathons/HACIK2024/anticipating latency/training_data.csv')
df2 = pd.read_csv('/content/drive/MyDrive/Datathons/HACIK2024/anticipating latency/testing_data.csv')
train = df1.copy()
test = df2.copy()
label_encoder = LabelEncoder()
train['cpu_type'] = label_encoder.fit_transform(train['cpu_type'])
test['cpu_type'] = label_encoder.transform(test['cpu_type'])

train['timestamp'] = pd.to_datetime(train['timestamp'])
train['hour'] = train['timestamp'].dt.hour
train['day'] = train['timestamp'].dt.day
train['month'] = train['timestamp'].dt.month
train.drop('timestamp', axis=1, inplace=True)

test['timestamp'] = pd.to_datetime(test['timestamp'])
test['hour'] = test['timestamp'].dt.hour
test['day'] = test['timestamp'].dt.day
test['month'] = test['timestamp'].dt.month
test.drop('timestamp', axis=1, inplace=True)
# Function to convert ram_limit from megabytes to bytes
def convert_ram_limit_to_bytes(ram_limit):
    return int(ram_limit.replace('M', '')) * (2 ** 20)

# Apply the function to the ram_limit column
train['ram_limit'] = train['ram_limit'].apply(convert_ram_limit_to_bytes)
test['ram_limit'] = test['ram_limit'].apply(convert_ram_limit_to_bytes)
X_train = train.drop(['ID','latency'], axis=1)
y_train = train['latency']
X_test = test


In [ ]:
X_train['log_cpu_usage'] = np.log1p(X_train['cpu_usage'])
X_train['log_ram_usage'] = np.log1p(X_train['ram_usage'])
X_train['cpu_ram_ratio'] = X_train['cpu_limit'] / X_train['ram_limit']
X_train['cpu_usage_ratio'] = X_train['cpu_usage'] / X_train['cpu_limit']
X_train['ram_usage_ratio'] = X_train['ram_usage'] / X_train['ram_limit']
X_train['req_per_client'] = X_train['num_req'] / X_train['conc_lvl']
X_train['total_memory_usage'] = X_train['ram_limit'] + X_train['ram_usage']

In [ ]:
scaler = StandardScaler()
#minmax = MinMaxScaler()
train_scaled = scaler.fit_transform(X_train)

In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.ensemble import BaggingRegressor, RandomForestRegressor, ExtraTreesRegressor, HistGradientBoostingRegressor
from sklearn.tree import DecisionTreeRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor
from catboost import CatBoostRegressor

models = {
    'RandomForestRegressor': RandomForestRegressor(),
    'XGBRegressor': XGBRegressor(objective='reg:squarederror', random_state=42),
    'ExtraTreesRegressor': ExtraTreesRegressor(),
    'LGBMRegressor': LGBMRegressor(verbose=0),
    'CatBoostRegressor': CatBoostRegressor(verbose=0),
}

# Cross-validate each model and print R-squared scores
for name, model in models.items():
    scores = cross_val_score(model, train_scaled, y_train, cv=5, scoring='r2')
    print(f'{name}: R-squared = {np.mean(scores):.4f} (mean), {np.std(scores):.4f} (std)')


BaggingRegressor: R-squared = 0.9713 (mean), 0.0056 (std)
RandomForestRegressor: R-squared = 0.9747 (mean), 0.0052 (std)
XGBRegressor: R-squared = 0.9736 (mean), 0.0047 (std)
ExtraTreesRegressor: R-squared = 0.9759 (mean), 0.0043 (std)
HistGradientBoostingRegressor: R-squared = 0.9706 (mean), 0.0039 (std)
LGBMRegressor: R-squared = 0.9724 (mean), 0.0045 (std)
DecisionTreeRegressor: R-squared = 0.9541 (mean), 0.0080 (std)
CatBoostRegressor: R-squared = 0.9745 (mean), 0.0043 (std)


In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import cross_val_score
from xgboost import XGBRegressor
import optuna
from optuna.samplers import TPESampler
import warnings

# Disable all warnings
warnings.filterwarnings('ignore')

# Define the objective function
def objective(trial):
    # Define the hyperparameters to tune
    params = {
        'n_estimators': trial.suggest_int('n_estimators', 50, 1000),
        'max_depth': trial.suggest_int('max_depth', 3, 20),
        'learning_rate': trial.suggest_loguniform('learning_rate', 1e-3, 0.1),
        'subsample': trial.suggest_uniform('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_uniform('colsample_bytree', 0.5, 1.0),
        'gamma': trial.suggest_loguniform('gamma', 1e-8, 1.0),
        'reg_alpha': trial.suggest_loguniform('reg_alpha', 1e-8, 1.0),
        'reg_lambda': trial.suggest_loguniform('reg_lambda', 1e-8, 1.0),
        'random_state': 42
    }

    # Create the model with the hyperparameters
    model = XGBRegressor(**params, objective='reg:squarederror')

    # Perform 5-fold cross-validation
    scores = cross_val_score(model, train_scaled, y_train, cv=5, scoring='r2')

    # Return the mean R-squared score
    return np.mean(scores)

# Create the study
study = optuna.create_study(direction='maximize', sampler=TPESampler(seed=42))

# Optimize the objective function
study.optimize(objective, n_trials=50)

# Print the best hyperparameters
print(f'Best trial: {study.best_trial.params}')

# Get the best hyperparameters
best_params = study.best_trial.params

# Train the model with the best hyperparameters
best_model = XGBRegressor(**best_params, objective='reg:squarederror')

# Perform 5-fold cross-validation with the best model
scores = cross_val_score(best_model, train_scaled, y_train, cv=5, scoring='r2')
print(f'Best XGBRegressor: R-squared = {np.mean(scores):.4f} (mean), {np.std(scores):.4f} (std)')


[I 2024-06-28 13:30:32,880] A new study created in memory with name: no-name-212ff099-a9b6-4792-9b88-31706b4bfa4d
[I 2024-06-28 13:37:05,126] Trial 0 finished with value: 0.9203693130308072 and parameters: {'n_estimators': 406, 'max_depth': 20, 'learning_rate': 0.029106359131330698, 'subsample': 0.7993292420985183, 'colsample_bytree': 0.5780093202212182, 'gamma': 1.7699302940633311e-07, 'reg_alpha': 2.9152036385288193e-08, 'reg_lambda': 0.08499808989182997}. Best is trial 0 with value: 0.9203693130308072.
[I 2024-06-28 13:43:14,488] Trial 1 finished with value: 0.7183658481850339 and parameters: {'n_estimators': 621, 'max_depth': 15, 'learning_rate': 0.0010994335574766201, 'subsample': 0.9849549260809971, 'colsample_bytree': 0.9162213204002109, 'gamma': 4.997040685255803e-07, 'reg_alpha': 2.8483918709107956e-07, 'reg_lambda': 2.9324868872723725e-07}. Best is trial 0 with value: 0.9203693130308072.
[I 2024-06-28 13:44:15,340] Trial 2 finished with value: 0.9626174938077184 and parameter

Best trial: {'n_estimators': 891, 'max_depth': 9, 'learning_rate': 0.011491756208808674, 'subsample': 0.6798583051138611, 'colsample_bytree': 0.9711361850258492, 'gamma': 0.044180632492090754, 'reg_alpha': 1.5212535876550204e-06, 'reg_lambda': 8.101413800984314e-05}
Best XGBRegressor: R-squared = 0.9750 (mean), 0.0036 (std)


In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, cross_val_score
import optuna
from optuna.samplers import TPESampler
from lightgbm import LGBMRegressor
import warnings

# Disable all warnings
warnings.filterwarnings('ignore')


def objective(trial):
    # Define the hyperparameters to tune
    params = {
        'num_leaves': trial.suggest_int('num_leaves', 20, 300),
        'max_depth': trial.suggest_int('max_depth', 3, 20),
        'learning_rate': trial.suggest_loguniform('learning_rate', 1e-3, 0.1),
        'n_estimators': trial.suggest_int('n_estimators', 50, 1000),
        'min_child_samples': trial.suggest_int('min_child_samples', 5, 100),
        'subsample': trial.suggest_uniform('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_uniform('colsample_bytree', 0.5, 1.0),
        'reg_alpha': trial.suggest_loguniform('reg_alpha', 1e-8, 1.0),
        'reg_lambda': trial.suggest_loguniform('reg_lambda', 1e-8, 1.0),
        'random_state': 42
    }

    # Create the model with the hyperparameters
    model = LGBMRegressor(**params)

    # Perform 5-fold cross-validation
    scores = cross_val_score(model, train_scaled, y_train, cv=5, scoring='r2')

    # Return the mean R-squared score
    return np.mean(scores)

# Create the study
study = optuna.create_study(direction='maximize', sampler=TPESampler(seed=42))

# Optimize the objective function
study.optimize(objective, n_trials=50)

# Print the best hyperparameters
print(f'Best trial: {study.best_trial.params}')

# Get the best hyperparameters
best_params = study.best_trial.params

# Train the model with the best hyperparameters
best_model = LGBMRegressor(**best_params)

# Perform 5-fold cross-validation with the best model
scores = cross_val_score(best_model, X_train, y_train, cv=5, scoring='r2')
print(f'Best LGBMRegressor: R-squared = {np.mean(scores):.4f} (mean), {np.std(scores):.4f} (std)')


[I 2024-06-28 15:35:17,652] A new study created in memory with name: no-name-e8a6bb6b-977a-4d2c-bb0b-1f8588bf7037


[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001107 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6450144.984593
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002818 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6473780.290151
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002810 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the 

[I 2024-06-28 15:35:36,893] Trial 0 finished with value: 0.9672049943021082 and parameters: {'num_leaves': 125, 'max_depth': 20, 'learning_rate': 0.029106359131330698, 'n_estimators': 619, 'min_child_samples': 19, 'subsample': 0.5779972601681014, 'colsample_bytree': 0.5290418060840998, 'reg_alpha': 0.08499808989182997, 'reg_lambda': 0.0006440507553993703}. Best is trial 0 with value: 0.9672049943021082.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003185 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6450144.984593
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive 

[I 2024-06-28 15:35:45,256] Trial 1 finished with value: 0.9537743893034312 and parameters: {'num_leaves': 218, 'max_depth': 3, 'learning_rate': 0.08706020878304858, 'n_estimators': 841, 'min_child_samples': 25, 'subsample': 0.5909124836035503, 'colsample_bytree': 0.5917022549267169, 'reg_alpha': 2.716051144654844e-06, 'reg_lambda': 0.00015777981883364995}. Best is trial 0 with value: 0.9672049943021082.


...

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005742 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6450144.984593
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003087 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6473780.290151
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003126 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] 

[I 2024-06-28 15:55:38,940] Trial 48 finished with value: 0.9734299900280188 and parameters: {'num_leaves': 38, 'max_depth': 17, 'learning_rate': 0.05601452188305111, 'n_estimators': 917, 'min_child_samples': 10, 'subsample': 0.620721334824011, 'colsample_bytree': 0.6995673235974937, 'reg_alpha': 0.07797291329312488, 'reg_lambda': 7.437749429847792e-05}. Best is trial 37 with value: 0.9734303584620599.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005800 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6450144.984593
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005454 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6473780.290151
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003153 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 757
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] 

[I 2024-06-28 15:55:51,323] Trial 49 finished with value: 0.9739708827524804 and parameters: {'num_leaves': 36, 'max_depth': 19, 'learning_rate': 0.06473825213531798, 'n_estimators': 925, 'min_child_samples': 8, 'subsample': 0.6073464352869796, 'colsample_bytree': 0.6929196262576613, 'reg_alpha': 0.05145624827172174, 'reg_lambda': 6.061837507091329e-06}. Best is trial 49 with value: 0.9739708827524804.


Best trial: {'num_leaves': 36, 'max_depth': 19, 'learning_rate': 0.06473825213531798, 'n_estimators': 925, 'min_child_samples': 8, 'subsample': 0.6073464352869796, 'colsample_bytree': 0.6929196262576613, 'reg_alpha': 0.05145624827172174, 'reg_lambda': 6.061837507091329e-06}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003170 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 755
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6450144.984593
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005628 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 755
[LightGBM] [Info] Number of data points in the train set: 32907, number of used features: 10
[LightGBM] [Info] Start training from score 6473780.290151
[LightGBM] [Info] Auto-choosing

In [ ]:
xgbm Best trial: {'num_leaves': 36, 'max_depth': 19, 'learning_rate': 0.06473825213531798, 'n_estimators': 925, 'min_child_samples': 8,
             'subsample': 0.6073464352869796, 'colsample_bytree': 0.6929196262576613, 'reg_alpha': 0.05145624827172174, 'reg_lambda': 6.061837507091329e-06}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003170 seconds.